In [2]:
# x>=1.5 in ./.env/lib/python3.9/site-packages (from python-dateutil>=2.8.1->pandas>=1.5.0->fastparquet) (1.16.0)
# Installing collected packages: fsspec, cramjam, fastparquet
# Successfully installed cramjam-2.6.2 fastparquet-2023.4.0 fsspec-2023.5.0

In [3]:
pd.io.parquet.PyArrowImpl()

In [3]:
import pandas as pd

data = pd.read_parquet("../data/transformed/validated_rides_2023_02.parquet")
data.head()

ImportError: Unable to find a usable engine; tried using: 'pyarrow', 'fastparquet'.
A suitable version of pyarrow or fastparquet is required for parquet support.
Trying to import the above resulted in these errors:
 - Missing optional dependency 'pyarrow'. pyarrow is required for parquet support. Use pip or conda to install pyarrow.
 - Missing optional dependency 'fastparquet'. fastparquet is required for parquet support. Use pip or conda to install fastparquet.

In [5]:
data['pickup_hour'] = data['pickup_datetime'].dt.floor('H')

In [6]:
data.head(10)

pickup_datetime  pickup_location_id pickup_hour
0 2023-02-01 00:32:53                 142  2023-02-01
1 2023-02-01 00:35:16                  71  2023-02-01
2 2023-02-01 00:35:16                  71  2023-02-01
3 2023-02-01 00:29:33                 132  2023-02-01
4 2023-02-01 00:12:28                 161  2023-02-01
5 2023-02-01 00:52:40                 148  2023-02-01
6 2023-02-01 00:12:39                 137  2023-02-01
7 2023-02-01 00:56:53                 263  2023-02-01
8 2023-02-01 00:20:40                  48  2023-02-01
9 2023-02-01 00:33:51                 114  2023-02-01

In [7]:
agg_rides = data.groupby(['pickup_hour','pickup_location_id']).size().reset_index()
agg_rides.rename(columns = {0:'rides'},inplace = True)

In [8]:
agg_rides.head()

pickup_hour  pickup_location_id  rides
0  2023-02-01                   4      4
1  2023-02-01                  10      1
2  2023-02-01                  11      1
3  2023-02-01                  13      2
4  2023-02-01                  22      1

In [9]:
from tqdm import tqdm

def add_missing_slots(agg_rides : pd.DataFrame) ->pd.DataFrame:
    location_ids = agg_rides['pickup_location_id'].unique()
    full_range_dates = pd.date_range(
        agg_rides['pickup_hour'].min(), agg_rides['pickup_hour'].max (), freq = 'H'
    )

    output = pd.DataFrame()
    for location_id in location_ids:

        # keep only rides for this location ids
        agg_rides_i = agg_rides.loc[agg_rides['pickup_location_id']== location_id, ['pickup_hour', 'rides']]

        # fill 0's
        agg_rides_i.set_index('pickup_hour', inplace=True)
        agg_rides_i.index = pd.DatetimeIndex(agg_rides_i.index)
        agg_rides_i = agg_rides_i.reindex(full_range_dates, fill_value=0)

        # add back location_id columns
        agg_rides_i['pickup_location_id'] = location_id

        output = pd.concat([output, agg_rides_i])


    # move purchase_day from index to dataframe column

    output = output.reset_index().rename(columns={'index':"pickup_hour"})

    return output

In [10]:
agg_rides_all_slots = add_missing_slots(agg_rides)

In [11]:
agg_rides_all_slots.head()

pickup_hour  rides  pickup_location_id
0 2023-02-01 00:00:00      4                   4
1 2023-02-01 01:00:00      7                   4
2 2023-02-01 02:00:00      0                   4
3 2023-02-01 03:00:00      0                   4
4 2023-02-01 04:00:00      0                   4

In [12]:
from typing import Optional, List
import plotly.express as px

def plot_rides(
    rides: pd.DataFrame,
    locations: Optional[List[int]] = None):
    """
    plot time series data
    """

    rides_to_plot = rides[rides['pickup_location_id'].isin(locations)] if locations else rides 
 
    fig  = px.line(rides_to_plot,
    x='pickup_hour',
    y = 'rides',
    color= 'pickup_location_id',
    template='none',
    )

    fig.show()

In [13]:
plot_rides(agg_rides_all_slots)

In [14]:
plot_rides(agg_rides_all_slots, locations=[43])

In [15]:
agg_rides_all_slots.to_parquet("../data/transformed/ts_data_rides_2023_02.parquet")